In [1]:
import pandas as pd
import math
import numpy as np
import copy
from sklearn.preprocessing import LabelEncoder
from xgboost import XGBClassifier, XGBRegressor
from lightgbm import LGBMClassifier, LGBMRegressor
!pip install catboost
from catboost import CatBoostClassifier, CatBoostRegressor
!pip install https://github.com/pandas-profiling/pandas-profiling/archive/master.zip
import pandas_profiling as pp
from sklearn.model_selection import train_test_split, KFold
from sklearn.metrics import mean_squared_error

     |████████████████████████████████| 67.3MB 62kB/s 
     / 38.4MB 71.8MB/s
     |████████████████████████████████| 81kB 7.0MB/s 
     |████████████████████████████████| 1.1MB 30.4MB/s 
     |████████████████████████████████| 3.2MB 37.9MB/s 
     |████████████████████████████████| 61kB 6.4MB/s 
     |████████████████████████████████| 81kB 9.3MB/s 
     |████████████████████████████████| 296kB 41.7MB/s 
  Created wheel for pandas-profiling: filename=pandas_profiling-2.12.0-py2.py3-none-any.whl size=243829 sha256=99127e0510ced6610dd17024868e3cc8d302fcdfa166200f1c3e046bd704719f
  Stored in directory: /tmp/pip-ephem-wheel-cache-isbsgjjf/wheels/56/c2/dd/8d945b0443c35df7d5f62fa9e9ae105a2d8b286302b92e0109
  Created wheel for htmlmin: filename=htmlmin-0.1.12-cp37-none-any.whl size=27085 sha256=4f9426449e96b35f601315b25c6673db42e13b4970324113eb1da79d4b348079
  Stored in directory: /root/.cache/pip/wheels/43/07/ac/7c5a9d708d65247ac1f94066cf1db075540b85716c30255459
  Created wheel for phik: fil

In [ ]:
from google.colab import drive
drive.mount('/content/drive')

Mounted at /content/drive


In [ ]:
!cp -r --recursive  "/content/drive/MyDrive/DataScienceCompetitions/HackerEarth_ReduceMarketingWaste/test.csv" "/content"
!cp -r --recursive  "/content/drive/MyDrive/DataScienceCompetitions/HackerEarth_ReduceMarketingWaste/train.csv" "/content"
!cp -r --recursive  "/content/drive/MyDrive/DataScienceCompetitions/HackerEarth_ReduceMarketingWaste/sample_submission.csv" "/content"

In [81]:
def df_details(df):
    arr1 = df.columns.tolist()
    arr2 = df.isnull().sum().tolist()
    arr3 = df.dtypes.tolist()
    arr4 = df.nunique().tolist()

    arr5 = []
    for i in df.columns:
        try:
            arr5.append(sum(df[i] < 0))
        except:
            arr5.append("type_error")



    df_new = {"feature":arr1, "null_values":arr2, "type":arr3, "unique values":arr4, "negative count":arr5}
    df_new = pd.DataFrame(df_new)
    return df_new

In [82]:
df_train = pd.read_csv("train.csv")
df_details(df_train)

feature  null_values     type  unique values negative count
0              Deal_title            0   object           7007     type_error
1               Lead_name            0   object           7007     type_error
2                Industry            1   object            171     type_error
3              Deal_value           51   object           6907     type_error
4         Weighted_amount          525   object           6480     type_error
5        Date_of_creation            0   object            777     type_error
6                   Pitch            0   object              2     type_error
7              Contact_no            0   object           7007     type_error
8            Lead_revenue            0   object              3     type_error
9           Fund_category            0   object              4     type_error
10              Geography          972   object              2     type_error
11               Location           11   object            597     type_error
12               POC_name            8   object           5261     type_error
13            Designation            0   object             10     type_error
14         Lead_POC_email            0   object           7007     type_error
15  Hiring_candidate_role            0   object            639     type_error
16            Lead_source            0   object              4     type_error
17       Level_of_meeting            0   object              3     type_error
18       Last_lead_update          633   object             11     type_error
19           Internal_POC            0   object             60     type_error
20               Resource          149   object              6     type_error
21        Internal_rating            0    int64              5              0
22    Success_probability            0  float64            248             70

In [ ]:
profile = pp.ProfileReport(df_train, title='train dataset Profiling Report', explorative=True)
profile.to_file("profile.html")
profile.to_notebook_iframe()

Summarize dataset:   0%|          | 0/36 [00:00<?, ?it/s]

Generate report structure:   0%|          | 0/1 [00:00<?, ?it/s]

Render HTML:   0%|          | 0/1 [00:00<?, ?it/s]

Export report to file:   0%|          | 0/1 [00:00<?, ?it/s]

In [83]:
df_train = pd.read_csv("train.csv")


df_train["Industry"]           =    df_train["Industry"].fillna("Banks")
df_train["POC_name"]           =    df_train["POC_name"].fillna("pooja")
df_train["Last_lead_update"]   =    df_train["Last_lead_update"].fillna("Following up but lead not responding")
df_train["Resource"]           =    df_train["Resource"].fillna("new_category")


def func1(x):
    if pd.isna(x):
        pass
    elif x[-1] == "$":
        return float(x[:-1])
    else:
        print(x)

df_train["Deal_value"] = df_train["Deal_value"].apply(func1)
df_train["Deal_value"] = df_train["Deal_value"].fillna(df_train.Deal_value.mean())



df_train["Weighted_amount"] = df_train["Weighted_amount"].apply(func1)
df_train["Weighted_amount"] = df_train["Weighted_amount"].fillna(df_train.Weighted_amount.mean())


# def func2(x):
    # if x<0:
        # return 0
    # elif x>100:
        # return 100
    # else:
    #     return x
# df_train["Success_probability"] = df_train["Success_probability"].apply(func2)
df_train = df_train[df_train['Success_probability'] <= 100] 
df_train = df_train[df_train['Success_probability'] >= 0] 


df_train["train"] = 1
print(df_train.shape)
df_train.head()

(6422, 24)


Deal_title                      Lead_name  ... Success_probability  train
0  TitleM5DZY  Davis, Perkins and Bishop Inc  ...                73.6      1
1  TitleKIW18                 Bender PLC LLC  ...                58.9      1
2  TitleFXSDN          Carter-Henry and Sons  ...                68.8      1
3  TitlePSK4Y                 Garcia Ltd Ltd  ...                64.5      1
4  Title904GV               Lee and Sons PLC  ...                62.4      1

[5 rows x 24 columns]

In [84]:
df_details(df_train)

feature  null_values     type  unique values negative count
0              Deal_title            0   object           6422     type_error
1               Lead_name            0   object           6422     type_error
2                Industry            0   object            171     type_error
3              Deal_value            0  float64           6339              0
4         Weighted_amount            0  float64           5947              0
5        Date_of_creation            0   object            777     type_error
6                   Pitch            0   object              2     type_error
7              Contact_no            0   object           6422     type_error
8            Lead_revenue            0   object              3     type_error
9           Fund_category            0   object              4     type_error
10              Geography          878   object              2     type_error
11               Location            9   object            597     type_error
12               POC_name            0   object           4864     type_error
13            Designation            0   object             10     type_error
14         Lead_POC_email            0   object           6422     type_error
15  Hiring_candidate_role            0   object            639     type_error
16            Lead_source            0   object              4     type_error
17       Level_of_meeting            0   object              3     type_error
18       Last_lead_update            0   object             11     type_error
19           Internal_POC            0   object             60     type_error
20               Resource            0   object              7     type_error
21        Internal_rating            0    int64              5              0
22    Success_probability            0  float64            246              0
23                  train            0    int64              1              0

In [ ]:
cols = ["Pitch", "Lead_revenue", "Fund_category", "Geography", "Location", "POC_name", "Designation", "Hiring_candidate_role",
          "Lead_source", "Level_of_meeting", "Last_lead_update", "Internal_POC", "Resource", "Internal_rating", "Success_probability"]
for i in cols:
    for j in cols:
        if i != j:
            df_group = df_train.groupby([i, j],as_index=False)
            print("total groups: ", len(df_group))
            print("uniques in ", i, df_train[i].nunique())
            print("uniques in ", j, df_train[j].nunique())
            print(df_group.size())
            print()
            print()


total groups:  6
uniques in  Pitch 2
uniques in  Lead_revenue 3
       Pitch             Lead_revenue  size
0  Product_1        100 - 500 Million  1084
1  Product_1         50 - 100 Million  1047
2  Product_1  500 Million - 1 Billion  1072
3  Product_2        100 - 500 Million  1071
4  Product_2         50 - 100 Million  1043
5  Product_2  500 Million - 1 Billion  1105


total groups:  8
uniques in  Pitch 2
uniques in  Fund_category 4
       Pitch Fund_category  size
0  Product_1    Category 1   814
1  Product_1    Category 2   802
2  Product_1    Category 3   809
3  Product_1    Category 4   778
4  Product_2    Category 1   794
5  Product_2    Category 2   828
6  Product_2    Category 3   831
7  Product_2    Category 4   766


total groups:  6
uniques in  Pitch 2
uniques in  Geography 2
       Pitch Geography  size
0  Product_1     India  1344
1  Product_1       USA  1432
2  Product_2     India  1399
3  Product_2       USA  1369


total groups:  1178
uniques in  Pitch 2
uniques in  Lo

In [85]:
df_test = pd.read_csv("test.csv")
df_details(df_test)

feature  null_values     type  unique values negative count
0              Deal_title            0   object           2093     type_error
1               Lead_name            0   object           2093     type_error
2                Industry            1   object            138     type_error
3              Deal_value            5   object           2083     type_error
4         Weighted_amount           60   object           2033     type_error
5        Date_of_creation            0   object            720     type_error
6                   Pitch            0   object              2     type_error
7              Contact_no            0   object           2093     type_error
8            Lead_revenue            0   object              3     type_error
9           Fund_category            0   object              4     type_error
10              Geography           79   object              2     type_error
11               Location            3   object            565     type_error
12               POC_name            2   object           1745     type_error
13            Designation            0   object             10     type_error
14         Lead_POC_email            0   object           2093     type_error
15  Hiring_candidate_role            0   object            618     type_error
16            Lead_source            0   object              4     type_error
17       Level_of_meeting            0   object              3     type_error
18       Last_lead_update          168   object             11     type_error
19           Internal_POC            0   object             60     type_error
20               Resource           14   object              6     type_error
21        Internal_rating            0  float64              7             48

In [ ]:
profile = pp.ProfileReport(df_test, title='test dataset Profiling Report', explorative=True)
profile.to_file("profile.html")
profile.to_notebook_iframe()

Summarize dataset:   0%|          | 0/35 [00:00<?, ?it/s]

Generate report structure:   0%|          | 0/1 [00:00<?, ?it/s]

Render HTML:   0%|          | 0/1 [00:00<?, ?it/s]

Export report to file:   0%|          | 0/1 [00:00<?, ?it/s]

In [86]:
df_test = pd.read_csv("test.csv")


df_test["Industry"]           =    df_test["Industry"].fillna("Banks")
df_test["POC_name"]           =    df_test["POC_name"].fillna("pooja")
df_test["Last_lead_update"]   =    df_test["Last_lead_update"].fillna("Following up but lead not responding")
df_test["Resource"]           =    df_test["Resource"].fillna("new_category")


def func1(x):
    if pd.isna(x):
        pass
    elif x[-1] == "$":
        return float(x[:-1])
    else:
        print(x)

df_test["Deal_value"] = df_test["Deal_value"].apply(func1)
df_test["Deal_value"] = df_test["Deal_value"].fillna(df_train.Deal_value.mean())



df_test["Weighted_amount"] = df_test["Weighted_amount"].apply(func1)
df_test["Weighted_amount"] = df_test["Weighted_amount"].fillna(df_train.Weighted_amount.mean())




def func2(x):
    if x<0:
        return abs(x)
    else:
        return x
df_test["Internal_rating"] = df_test["Internal_rating"].apply(func2)




df_test["train"] = 0
df_test["Success_probability"] = 99999
print(df_test.shape)
df_test.head()



(2093, 24)


Deal_title                       Lead_name  ... train  Success_probability
0  TitleAD16O                 Bonilla Ltd Inc  ...     0                99999
1  TitleOW6CR  Williams, Rogers and Roach PLC  ...     0                99999
2  TitleVVJQ5    Wood, Vaughn and Morales Ltd  ...     0                99999
3  TitleUS8NA             Durham-Crawford Inc  ...     0                99999
4  Title5VGWW    Simpson, Duncan and Long LLC  ...     0                99999

[5 rows x 24 columns]

In [87]:
df_details(df_test)

feature  null_values     type  unique values negative count
0              Deal_title            0   object           2093     type_error
1               Lead_name            0   object           2093     type_error
2                Industry            0   object            138     type_error
3              Deal_value            0  float64           2084              0
4         Weighted_amount            0  float64           2034              0
5        Date_of_creation            0   object            720     type_error
6                   Pitch            0   object              2     type_error
7              Contact_no            0   object           2093     type_error
8            Lead_revenue            0   object              3     type_error
9           Fund_category            0   object              4     type_error
10              Geography           79   object              2     type_error
11               Location            3   object            565     type_error
12               POC_name            0   object           1745     type_error
13            Designation            0   object             10     type_error
14         Lead_POC_email            0   object           2093     type_error
15  Hiring_candidate_role            0   object            618     type_error
16            Lead_source            0   object              4     type_error
17       Level_of_meeting            0   object              3     type_error
18       Last_lead_update            0   object             11     type_error
19           Internal_POC            0   object             60     type_error
20               Resource            0   object              7     type_error
21        Internal_rating            0  float64              6              0
22                  train            0    int64              1              0
23    Success_probability            0    int64              1              0

In [88]:
df = pd.concat([df_train,df_test])
df = df.reset_index(drop=True)
df = df.sample(frac=1)

print(df.shape)
df.head()

(8515, 24)


Deal_title                        Lead_name  ... Success_probability  train
5034  TitleX0DDX                    Joyce Ltd LLC  ...                69.1      1
3253  TitleZT2D2               Ortiz LLC and Sons  ...                64.2      1
6593  TitleQETZZ  Durham, Dickerson and Curry Inc  ...             99999.0      0
3993  TitleHHLQO                    Heath Inc PLC  ...                67.0      1
6390  TitleKXFMV     Conner, Jarvis and Adams PLC  ...                67.4      1

[5 rows x 24 columns]

In [68]:
# ind_loc = []
# usa_loc = []
# unknown = []
# ct = 0
# for ind in range(len(df)):
#     try:
#         i = df["Geography"][ind]
#         if i == "USA":
#             usa_loc.append(df["Location"][ind])
#         elif i == "India":
#             ind_loc.append(df["Location"][ind])
#         else:
#             unknown.append(df["Location"][ind])
#     except:
#         ct = ct + 1

# print(ct)
# print(len(ind_loc), len(set(ind_loc)))
# print(len(usa_loc), len(set(usa_loc)))
# print(len(unknown), len(set(unknown)))
# print(ind_loc)
# print(usa_loc)
# print(unknown)


# ind_loc.extend(usa_loc)
# print(len(ind_loc), len(set(ind_loc)))


# ind_loc.extend(unknown)
# print(len(ind_loc), len(set(ind_loc)))




In [89]:
ind_loc = []
usa_loc = []
for ind in range(len(df)):
    try:
        i = df["Geography"][ind]
        if i == "USA":
            usa_loc.append(df["Location"][ind])
        elif i == "India":
            ind_loc.append(df["Location"][ind])
    except:
        pass


for ind in range(len(df)):
    geo = df["Geography"][ind]
    loct = df["Location"][ind]
    if loct in ind_loc:
        df["Geography"][ind] = "India"
    elif loct in usa_loc:
        df["Geography"][ind] = "USA"



df["Location"]      =    df["Location"].fillna("new_val")


# def func4(x):
#     if   x>=0  and x<10:return 1
#     elif x>=10 and x<20:return 2
#     elif x>=20 and x<30:return 3
#     elif x>=30 and x<40:return 4
#     elif x>=40 and x<50:return 5
#     elif x>=50 and x<60:return 6
#     elif x>=60 and x<70:return 7
#     elif x>=70 and x<80:return 8
#     elif x>=80 and x<90:return 9
#     elif x>=90 and x<=100:return 10
#     elif x==99999:
#         return 10
# df["Success_probability"] = df["Success_probability"].apply(func4)

print(df.shape)
df.head()

/usr/local/lib/python3.7/dist-packages/ipykernel_launcher.py:20: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
/usr/local/lib/python3.7/dist-packages/ipykernel_launcher.py:18: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy


(8515, 24)


Deal_title                        Lead_name  ... Success_probability  train
5034  TitleX0DDX                    Joyce Ltd LLC  ...                69.1      1
3253  TitleZT2D2               Ortiz LLC and Sons  ...                64.2      1
6593  TitleQETZZ  Durham, Dickerson and Curry Inc  ...             99999.0      0
3993  TitleHHLQO                    Heath Inc PLC  ...                67.0      1
6390  TitleKXFMV     Conner, Jarvis and Adams PLC  ...                67.4      1

[5 rows x 24 columns]

In [90]:
df_details(df)

feature  null_values     type  unique values negative count
0              Deal_title            0   object           8515     type_error
1               Lead_name            0   object           8515     type_error
2                Industry            0   object            172     type_error
3              Deal_value            0  float64           8403              0
4         Weighted_amount            0  float64           7981              0
5        Date_of_creation            0   object            777     type_error
6                   Pitch            0   object              2     type_error
7              Contact_no            0   object           8515     type_error
8            Lead_revenue            0   object              3     type_error
9           Fund_category            0   object              4     type_error
10              Geography            0   object              2     type_error
11               Location            0   object            598     type_error
12               POC_name            0   object           6247     type_error
13            Designation            0   object             10     type_error
14         Lead_POC_email            0   object           8514     type_error
15  Hiring_candidate_role            0   object            639     type_error
16            Lead_source            0   object              4     type_error
17       Level_of_meeting            0   object              3     type_error
18       Last_lead_update            0   object             11     type_error
19           Internal_POC            0   object             60     type_error
20               Resource            0   object              7     type_error
21        Internal_rating            0  float64              6              0
22    Success_probability            0  float64            247              0
23                  train            0    int64              2              0

In [91]:
le = LabelEncoder()
df["Industry"] = le.fit_transform(df["Industry"])

le = LabelEncoder()
df["Pitch"] = le.fit_transform(df["Pitch"])

le = LabelEncoder()
df["Lead_revenue"] = le.fit_transform(df["Lead_revenue"])

le = LabelEncoder()
df["Fund_category"] = le.fit_transform(df["Fund_category"])

le = LabelEncoder()
df["Geography"] = le.fit_transform(df["Geography"])

le = LabelEncoder()
df["Location"] = le.fit_transform(df["Location"])

le = LabelEncoder()
df["Designation"] = le.fit_transform(df["Designation"])

le = LabelEncoder()
df["Hiring_candidate_role"] = le.fit_transform(df["Hiring_candidate_role"])

le = LabelEncoder()
df["Lead_source"] = le.fit_transform(df["Lead_source"])

le = LabelEncoder()
df["Level_of_meeting"] = le.fit_transform(df["Level_of_meeting"])

le = LabelEncoder()
df["Last_lead_update"] = le.fit_transform(df["Last_lead_update"])

le = LabelEncoder()
df["Internal_POC"] = le.fit_transform(df["Internal_POC"])

le = LabelEncoder()
df["Resource"] = le.fit_transform(df["Resource"])





print(df.shape)
df.head()

(8515, 24)


Deal_title                        Lead_name  ...  Success_probability  train
5034  TitleX0DDX                    Joyce Ltd LLC  ...                 69.1      1
3253  TitleZT2D2               Ortiz LLC and Sons  ...                 64.2      1
6593  TitleQETZZ  Durham, Dickerson and Curry Inc  ...              99999.0      0
3993  TitleHHLQO                    Heath Inc PLC  ...                 67.0      1
6390  TitleKXFMV     Conner, Jarvis and Adams PLC  ...                 67.4      1

[5 rows x 24 columns]

In [92]:
df["DATE"] = pd.to_datetime(df['Date_of_creation'])
print(df.shape)

df["mon"] = df["DATE"].dt.month
df["yr"] = df["DATE"].dt.year
df["day"] = df["DATE"].dt.day
print(df.shape)
df.head()

(8515, 25)
(8515, 28)


Deal_title                        Lead_name  Industry  ...  mon    yr day
5034  TitleX0DDX                    Joyce Ltd LLC        10  ...    2  2019  24
3253  TitleZT2D2               Ortiz LLC and Sons        17  ...   11  2020   6
6593  TitleQETZZ  Durham, Dickerson and Curry Inc        47  ...   12  2020  13
3993  TitleHHLQO                    Heath Inc PLC        17  ...    9  2019  17
6390  TitleKXFMV     Conner, Jarvis and Adams PLC        93  ...    2  2020   5

[5 rows x 28 columns]

In [93]:
df = df.sample(frac=1)

train = df[df["train"]==1]
train = train.reset_index(drop=True)
print(train.shape)

test = df[df["train"]==0]
test = test.reset_index(drop=True)
print(test.shape)

test.head()

(6422, 28)
(2093, 28)


Deal_title                        Lead_name  Industry  ...  mon    yr day
0  TitleW7GAO                     King Ltd PLC        17  ...    7  2020   2
1  TitleX8GD0                 Rios Group Group        62  ...    6  2019   7
2  TitleTYKX4               Garza-Robles Group        32  ...   10  2020  24
3  TitleS73N4      Clark, Martin and Davis LLC        17  ...    1  2021  15
4  Title8Q2VE  Oconnell, Ross and Miller Group        25  ...    5  2019  28

[5 rows x 28 columns]

In [94]:

def training(X, Y):
    # model = XGBRegressor(n_estimators=100 , max_depth=8, verbosity=0, objective="reg:squarederror")
    # model = LGBMRegressor(max_depth=9 , n_estimators=120 , num_leaves=50)
    # model = CatBoostRegressor(n_estimators=800, depth=5, verbose=10)


    err = []
    kf = KFold(n_splits=5, shuffle=True, random_state=42) 
    for train_index, test_index in kf.split(X):
        # model = LGBMRegressor(max_depth=1 , n_estimators=120 , num_leaves=50)
        model = XGBRegressor(n_estimators=1000 , max_depth=1, verbosity=0, objective="reg:squarederror")
        # model = CatBoostRegressor(n_estimators=500, depth=1, verbose=0)



        print("Train:", train_index, "Validation:",test_index)
        X_train, X_test = X.iloc[train_index], X.iloc[test_index] 
        y_train, y_test = Y[train_index], Y[test_index]

        model.fit(X_train, y_train)

        
        err.append(max(0, 100 - np.sqrt(mean_squared_error(y_test, model.predict(X_test)))))

    print()
    print(err)
    print(sum(err)/len(err))


    # model.fit(X, Y)
    return model


def testing(X):
    ans = model.predict(X)
    return ans



In [95]:
col_to_drop = ["train", "Success_probability", "Deal_title", "Lead_name", "Date_of_creation", "Contact_no", "POC_name", "Lead_POC_email", "DATE", "day", "mon", "yr"]
trainX = train.drop(col_to_drop, axis=1)
print(trainX.columns)
print(trainX.shape)


trainY = train["Success_probability"]
print(trainY.shape)
print()
model = training(trainX, trainY)


Index(['Industry', 'Deal_value', 'Weighted_amount', 'Pitch', 'Lead_revenue',
       'Fund_category', 'Geography', 'Location', 'Designation',
       'Hiring_candidate_role', 'Lead_source', 'Level_of_meeting',
       'Last_lead_update', 'Internal_POC', 'Resource', 'Internal_rating'],
      dtype='object')
(6422, 16)
(6422,)

Train: [   0    1    2 ... 6419 6420 6421] Validation: [   8   14   15 ... 6409 6413 6417]
Train: [   0    1    2 ... 6418 6419 6420] Validation: [  12   26   30 ... 6415 6416 6421]
Train: [   1    2    3 ... 6418 6419 6421] Validation: [   0    6    7 ... 6389 6414 6420]
Train: [   0    3    4 ... 6417 6420 6421] Validation: [   1    2   10 ... 6405 6418 6419]
Train: [   0    1    2 ... 6419 6420 6421] Validation: [   3    4    5 ... 6406 6408 6412]

[88.43229921767616, 89.00926356546644, 89.15023814003993, 88.92997135633615, 88.33824393254092]
88.77200324241193


In [96]:
testX = test.drop(col_to_drop, axis=1)
print(testX.shape)
ans = testing(testX)
print(ans.shape)


# newans = copy.deepcopy(ans)
# print(newans.shape)

# ans = []
# for i in newans:
#     if i==1:ans.append(5)
#     if i==2:ans.append(15)
#     if i==3:ans.append(25)
#     if i==4:ans.append(35)
#     if i==5:ans.append(45)
#     if i==6:ans.append(55)
#     if i==7:ans.append(65)
#     if i==8:ans.append(75)
#     if i==9:ans.append(85)
#     if i==10:ans.append(95)

# print(len(ans))

(2093, 16)
(2093,)


In [98]:
#xgb


sample_sub = pd.read_csv("sample_submission.csv")
arr1 = []
arr2 = []

for ind in range(len(test)):
    j = test["Deal_title"][ind]
    arr1.append(j)
    arr2.append(ans[ind])


print(len(arr1), len(arr2))

dic = {"Deal_title": arr1, "Success_probability":arr2}
df_fin = pd.DataFrame(dic)

filename = "aaaaaaaaa.csv"

df_fin.to_csv(filename , index=False)
from google.colab import files
files.download(filename)

2093 2093


<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

In [37]:
l = pd.read_csv("lgbm.csv")
c = pd.read_csv("cat.csv")
x = pd.read_csv("xgb.csv")
r = pd.read_csv("random.csv")



ll = l.sort_values(['Deal_title']).reset_index(drop=True)
cc = c.sort_values(["Deal_title"]).reset_index(drop=True)
xx = x.sort_values(["Deal_title"]).reset_index(drop=True)
rr = r.sort_values(["Deal_title"]).reset_index(drop=True)



arr1 = []
arr2 = []
for i in  range(len(l)):
    title = ll["Deal_title"][i]

    a1 = ll["Success_probability"][i]
    a2 = cc["Success_probability"][i]
    a3 = xx["Success_probability"][i]
    a4 = rr["Success_probability"][i]


    avg = (a1 + a2 + a3 + a4)/4     

    arr1.append(title)
    arr2.append(avg)


print(len(arr1), len(arr2))

dic = {"Deal_title": arr1, "Success_probability":arr2}
df_fin = pd.DataFrame(dic)

filename = "final.csv"

df_fin.to_csv(filename , index=False)
from google.colab import files
files.download(filename)

2093 2093


<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>